In [1]:
import pandas as pd
import numpy as np
import pickle
import time
import scipy
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import KFold
from sklearn.model_selection import train_test_split

# Import train data

import recipe_train.csv

In [2]:
base_data = pd.read_csv("recipe_train.csv").values

In [3]:
base_data_df = pd.read_csv("recipe_train.csv")

seperate n_steps and n_ingredients

In [4]:
n_steps_ingr = []
for i in range(len(base_data)):
    lst = []
    for j in [1,2]:
        lst.append(base_data[i][j])
    n_steps_ingr.append(lst)
    
n_steps_ingr = np.array(n_steps_ingr)

In [5]:
n_steps_ingr_df = pd.DataFrame(n_steps_ingr, columns = ['n_steps', 'n_ingr'])

seperate duration_label

In [6]:
duration_label = [i[-1] for i in base_data]
duration_label = np.array(duration_label)

In [7]:
duration_label_df = base_data_df['duration_label']

In [8]:
duration_label_df 

0        2.0
1        2.0
2        2.0
3        2.0
4        2.0
        ... 
39995    1.0
39996    2.0
39997    1.0
39998    2.0
39999    2.0
Name: duration_label, Length: 40000, dtype: float64

import vocabulary

In [9]:
# vocab_name = pickle.load(open("recipe_text_features_countvec/train_name_countvectorizer.pkl", "rb"))
# vocab_steps = pickle.load(open("recipe_text_features_countvec/train_steps_countvectorizer.pkl", "rb"))
# vocab_ingr = pickle.load(open("recipe_text_features_countvec/train_ingr_countvectorizer.pkl", "rb"))

import countvec

In [10]:
countvec_name = scipy.sparse.load_npz('recipe_text_features_countvec/train_name_vec.npz').toarray().astype('int8')
countvec_steps = scipy.sparse.load_npz('recipe_text_features_countvec/train_steps_vec.npz').toarray().astype('int8')
countvec_ingr = scipy.sparse.load_npz('recipe_text_features_countvec/train_ingr_vec.npz').toarray().astype('int8')

In [11]:
countvec_name.shape

(40000, 10892)

import doc2vec100

In [12]:
doc2vec_name = pd.read_csv('recipe_text_features_doc2vec100/train_name_doc2vec100.csv', header=None).values
doc2vec_steps = pd.read_csv('recipe_text_features_doc2vec100/train_steps_doc2vec100.csv', header=None).values
doc2vec_ingr = pd.read_csv('recipe_text_features_doc2vec100/train_ingr_doc2vec100.csv', header=None).values

doc2vec df

In [13]:
doc2vec_name_df = pd.read_csv('recipe_text_features_doc2vec100/train_name_doc2vec100.csv', names=['d2v100_name'+str(i) for i in range(1,101)])
doc2vec_steps_df = pd.read_csv('recipe_text_features_doc2vec100/train_steps_doc2vec100.csv', names=['d2v100_steps'+str(i) for i in range(1,101)])
doc2vec_ingr_df = pd.read_csv('recipe_text_features_doc2vec100/train_ingr_doc2vec100.csv', names=['d2v100_ingr'+str(i) for i in range(1,101)])

Merge selected features

In [14]:
arrays = [countvec_name, doc2vec_name, countvec_steps, doc2vec_steps, countvec_ingr, doc2vec_ingr, n_steps_ingr]
data = np.hstack(arrays)

In [15]:
countvec_name_df = pd.DataFrame(countvec_name, columns = ['cv_name'+str(i) for i in range(1, len(countvec_name[0])+1)])
countvec_steps_df = pd.DataFrame(countvec_steps, columns = ['cv_steps'+str(i) for i in range(1, len(countvec_steps[0])+1)])
countvec_ingr_df = pd.DataFrame(countvec_ingr, columns = ['cv_ingr'+str(i) for i in range(1, len(countvec_ingr[0])+1)])

Merge selected features to df

In [16]:
all_df = countvec_name_df.join(doc2vec_name_df).join(countvec_steps_df).join(doc2vec_steps_df).join(countvec_ingr_df).join(doc2vec_ingr_df).join(n_steps_ingr_df)

In [17]:
all_df

cv_name1  cv_name2  cv_name3  cv_name4  cv_name5  cv_name6  cv_name7  \
0             0         0         0         0         0         0         0   
1             0         0         0         0         0         0         0   
2             0         0         0         0         0         0         0   
3             0         0         0         0         0         0         0   
4             0         0         0         0         0         0         0   
...         ...       ...       ...       ...       ...       ...       ...   
39995         0         0         0         0         0         0         0   
39996         0         0         0         0         0         0         0   
39997         0         0         0         0         0         0         0   
39998         0         0         0         0         0         0         0   
39999         0         0         0         0         0         0         0   

       cv_name8  cv_name9  cv_name10  ...  d2v100_ingr93  d2v100_ingr94  \
0             0         0          0  ...      -0.250643       0.214695   
1             0         0          0  ...      -0.122143      -0.188637   
2             0         0          0  ...       0.127930      -0.271923   
3             0         0          0  ...      -0.259047       0.107682   
4             0         0          0  ...       0.131887       0.215795   
...         ...       ...        ...  ...            ...            ...   
39995         0         0          0  ...      -0.110938       0.007777   
39996         0         0          0  ...      -0.019811       0.015345   
39997         0         0          0  ...       0.111844       0.219837   
39998         0         0          0  ...      -0.157026      -0.158611   
39999         0         0          0  ...       0.137772       0.195448   

       d2v100_ingr95  d2v100_ingr96  d2v100_ingr97  d2v100_ingr98  \
0          -0.018045       0.395938      -0.057779       0.336876   
1           0.096245       0.296148       0.098384      -0.124963   
2          -0.188931      -0.154470      -0.174869      -0.341245   
3          -0.259195      -0.065767      -0.065660      -0.207306   
4           0.119587      -0.063841      -0.107087      -0.281038   
...              ...            ...            ...            ...   
39995      -0.021177       0.016590      -0.189764      -0.068398   
39996       0.050862       0.087614       0.594146       0.507868   
39997       0.034625       0.033108      -0.518219       0.229315   
39998       0.375092       0.225296      -0.409948      -0.642923   
39999      -0.206056       0.092833      -0.045537      -0.035035   

       d2v100_ingr99  d2v100_ingr100  n_steps  n_ingr  
0           0.230647        0.143468        6      12  
1          -0.195799       -0.210086        9       5  
2          -0.060525        0.080168       15      10  
3          -0.167152        0.492161       10       8  
4          -0.136156        0.063560        6       5  
...              ...             ...      ...     ...  
39995      -0.190228        0.083059        6      13  
39996       0.109975       -0.047240       15      16  
39997      -0.024256       -0.351173        5       8  
39998       0.512482       -0.925799        7      17  
39999      -0.058196        0.035302        6      11  

[40000 rows x 32067 columns]

In [18]:
del base_data 
del base_data_df
del arrays

# del duration_label_df 
del n_steps_ingr
del n_steps_ingr_df

del doc2vec_name
del doc2vec_steps
del doc2vec_ingr
del doc2vec_name_df
del doc2vec_steps_df
del doc2vec_ingr_df
del countvec_name_df
del countvec_steps_df
del countvec_ingr_df

In [19]:
import gc

gc.collect()

40

# Import test data

import recipe_train.csv

In [20]:
base_data_test = pd.read_csv("recipe_test.csv").values

seperate n_steps and n_ingredients

In [21]:
n_steps_ingr_test = []
for i in range(len(base_data_test)):
    lst = []
    for j in [1,2]:
        lst.append(base_data_test[i][j])
    n_steps_ingr_test.append(lst)
    
n_steps_ingr_test = np.array(n_steps_ingr_test)

In [22]:
n_steps_ingr_test_df = pd.DataFrame(n_steps_ingr_test, columns = ['n_steps', 'n_ingr'])

import vocabulary

In [23]:
# vocab_name = pickle.load(open("recipe_text_features_countvec/train_name_countvectorizer.pkl", "rb"))
# vocab_steps = pickle.load(open("recipe_text_features_countvec/train_steps_countvectorizer.pkl", "rb"))
# vocab_ingr = pickle.load(open("recipe_text_features_countvec/train_ingr_countvectorizer.pkl", "rb"))

import countvec

In [24]:
countvec_name_test = scipy.sparse.load_npz('recipe_text_features_countvec/test_name_vec.npz').toarray().astype('int8')
countvec_steps_test = scipy.sparse.load_npz('recipe_text_features_countvec/test_steps_vec.npz').toarray().astype('int8')
countvec_ingr_test = scipy.sparse.load_npz('recipe_text_features_countvec/test_ingr_vec.npz').toarray().astype('int8')

In [25]:
countvec_name_test_df = pd.DataFrame(countvec_name_test, columns = ['cv_name'+str(i) for i in range(1, len(countvec_name_test[0])+1)])
countvec_steps_test_df = pd.DataFrame(countvec_steps_test, columns = ['cv_steps'+str(i) for i in range(1, len(countvec_steps_test[0])+1)])
countvec_ingr_test_df = pd.DataFrame(countvec_ingr_test, columns = ['cv_ingr'+str(i) for i in range(1, len(countvec_ingr_test[0])+1)])

In [26]:
# countvec_name_test_df

import doc2vec100

In [27]:
doc2vec_name_test_df = pd.read_csv('recipe_text_features_doc2vec100/test_name_doc2vec100.csv', names=['d2v100_name_test'+str(i) for i in range(1,101)])
doc2vec_steps_test_df = pd.read_csv('recipe_text_features_doc2vec100/test_steps_doc2vec100.csv', names=['d2v100_steps_test'+str(i) for i in range(1,101)])
doc2vec_ingr_test_df = pd.read_csv('recipe_text_features_doc2vec100/test_ingr_doc2vec100.csv', names=['d2v100_ingr_test'+str(i) for i in range(1,101)])

In [28]:
doc2vec_name_test = doc2vec_name_test_df.values
doc2vec_steps_test = doc2vec_steps_test_df.values
doc2vec_ingr_test = doc2vec_ingr_test_df.values

Merge selected features

In [29]:
arrays_test = [countvec_name_test, doc2vec_name_test, countvec_steps_test, doc2vec_steps_test, countvec_ingr_test, doc2vec_ingr_test, n_steps_ingr_test]
data_test = np.hstack(arrays_test)

In [30]:
data_test.shape

(10000, 32067)

In [31]:
data_test_df = countvec_name_test_df.join(doc2vec_name_test_df).join(countvec_steps_test_df).join(doc2vec_steps_test_df).join(countvec_ingr_test_df).join(doc2vec_ingr_test_df).join(n_steps_ingr_test_df)

Release memory

In [32]:
import gc

del countvec_name_test
del countvec_steps_test
del countvec_ingr_test
del doc2vec_name_test
del doc2vec_steps_test
del doc2vec_ingr_test
del arrays_test

del countvec_name
del countvec_steps
del countvec_ingr



gc.collect()

100

In [33]:
# start = time.time()

# prediction_data = xgbc.predict(data_test)

# fin = time.time()

# print(fin-start, 'seconds')

In [34]:
# len(prediction_data)

In [35]:
def export_pred(prediction_data, filename):
    prediction_dict = {'id':  [i for i in range(1,len(prediction_data)+1)],'duration_label': prediction_data}
    pred_df = pd.DataFrame (prediction_dict, columns = ['id','duration_label'])
    filename = filename+".csv"
    pred_df.to_csv(filename, index=None)

    return pred_df

    

In [35]:
# prediction_dict = {'id':  [i for i in range(1,len(prediction_data)+1)],'duration_label': prediction_data}

# pred_df = pd.DataFrame (prediction_dict, columns = ['id','duration_label'])

In [36]:
# pred_df

In [37]:
# pred_df.to_csv("prediction.csv", index=None)

# Feature Selection

## Spliting train test for Kbest

In [36]:
# Core libraries
import pandas as pd

# Sklearn processing
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split

# Define the X (input) and y (target) features
X = all_df
y = duration_label_df

# Rescale the input features
scaler = MinMaxScaler(feature_range=(0,1))
X_ = scaler.fit_transform(X)
X = pd.DataFrame(X_, columns=X.columns)

In [37]:
# Filter Method
# Split into train (2/3) and test (1/3) sets
test_size = 0.2
seed = 7
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=test_size, random_state=seed)
print(X_train.shape)
print(X_test.shape)

(32000, 32067)
(8000, 32067)


In [56]:
# del X_train
# del X_test 
# del y_train
# # del y_test

In [57]:
gc.collect()

60

#### jump to either select f_reg or f_classif

## Chi-sq k = 5000

In [64]:
# Perform feature selection using a univariate statistical test
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2
kbest_chi = SelectKBest(score_func=chi2, k=5000)
kbest_chi.fit(X_train, y_train)

print("Feature selection", kbest_chi.get_support())
print("Feature scores", kbest_chi.scores_)
print("Selected features:", list(X.columns[kbest_chi.get_support()]))
print("Removed features:", list(X.columns[~kbest_chi.get_support()]))

Feature selection [ True False False ... False  True  True]
Feature scores [ 18.61986511          nan   1.26100473 ...   0.22061648 160.24623579
 125.92347966]
Selected features: ['cv_name1', 'cv_name7', 'cv_name15', 'cv_name16', 'cv_name18', 'cv_name24', 'cv_name26', 'cv_name51', 'cv_name52', 'cv_name65', 'cv_name71', 'cv_name80', 'cv_name97', 'cv_name125', 'cv_name153', 'cv_name175', 'cv_name177', 'cv_name180', 'cv_name183', 'cv_name193', 'cv_name203', 'cv_name204', 'cv_name206', 'cv_name216', 'cv_name219', 'cv_name233', 'cv_name259', 'cv_name261', 'cv_name285', 'cv_name296', 'cv_name304', 'cv_name311', 'cv_name317', 'cv_name318', 'cv_name332', 'cv_name333', 'cv_name351', 'cv_name353', 'cv_name354', 'cv_name370', 'cv_name377', 'cv_name386', 'cv_name422', 'cv_name424', 'cv_name432', 'cv_name442', 'cv_name444', 'cv_name459', 'cv_name487', 'cv_name490', 'cv_name510', 'cv_name516', 'cv_name528', 'cv_name535', 'cv_name538', 'cv_name540', 'cv_name546', 'cv_name551', 'cv_name562', 'cv_name5

In [65]:
# Transform (remove features not selected)
X_train_kbest_chi = kbest_chi.transform(X_train)
X_test_kbest_chi = kbest_chi.transform(X_test)

In [66]:
from sklearn.linear_model import LogisticRegression

Create logistic regression classfier

In [67]:
lrc_chi_clf = LogisticRegression(max_iter = 1000)

Test lrc on test,train. (0.2=test)

In [68]:
start = time.time()

lrc_chi_clf.fit(X_train_kbest_chi, y_train)

fin = time.time()

print(fin-start, 'seconds')

173.0242199897766 seconds


In [69]:
lrc_chi_clf.score(X_test_kbest_chi, y_test)

0.790875

In [71]:
lrc_chi_5k_accuracy = lrc_chi_clf.score(X_test_kbest_chi, y_test)
print(lrc_chi_5k_accuracy)

0.790875


0.790875

## Chi-sq k = 1k

In [72]:
# Perform feature selection using a univariate statistical test
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2
kbest_chi = SelectKBest(score_func=chi2, k=1000)
kbest_chi.fit(X_train, y_train)

print("Feature selection", kbest_chi.get_support())
print("Feature scores", kbest_chi.scores_)
print("Selected features:", list(X.columns[kbest_chi.get_support()]))
print("Removed features:", list(X.columns[~kbest_chi.get_support()]))

Feature selection [False False False ... False  True  True]
Feature scores [ 18.61986511          nan   1.26100473 ...   0.22061648 160.24623579
 125.92347966]
Selected features: ['cv_name180', 'cv_name444', 'cv_name535', 'cv_name538', 'cv_name551', 'cv_name567', 'cv_name596', 'cv_name676', 'cv_name677', 'cv_name747', 'cv_name748', 'cv_name775', 'cv_name854', 'cv_name874', 'cv_name1017', 'cv_name1019', 'cv_name1131', 'cv_name1231', 'cv_name1288', 'cv_name1302', 'cv_name1338', 'cv_name1339', 'cv_name1342', 'cv_name1362', 'cv_name1388', 'cv_name1400', 'cv_name1467', 'cv_name1480', 'cv_name1507', 'cv_name1525', 'cv_name1567', 'cv_name1711', 'cv_name1714', 'cv_name1741', 'cv_name1917', 'cv_name1977', 'cv_name1999', 'cv_name2064', 'cv_name2078', 'cv_name2095', 'cv_name2203', 'cv_name2212', 'cv_name2251', 'cv_name2348', 'cv_name2349', 'cv_name2352', 'cv_name2358', 'cv_name2381', 'cv_name2514', 'cv_name2527', 'cv_name2531', 'cv_name2560', 'cv_name2599', 'cv_name2617', 'cv_name2777', 'cv_name2

In [73]:
# Transform (remove features not selected)
X_train_kbest_chi = kbest_chi.transform(X_train)
X_test_kbest_chi = kbest_chi.transform(X_test)

In [74]:
from sklearn.linear_model import LogisticRegression

Create logistic regression classfier

In [75]:
lrc_chi_clf = LogisticRegression(max_iter = 1000)

Test lrc on test,train. (0.2=test)

In [76]:
start = time.time()

lrc_chi_clf.fit(X_train_kbest_chi, y_train)

fin = time.time()

print(fin-start, 'seconds')

12.530497074127197 seconds


In [77]:
lrc_chi_clf.score(X_test_kbest_chi, y_test)

0.793875

## Chi-sq k = 750

In [113]:
# Perform feature selection using a univariate statistical test
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2
kbest_chi = SelectKBest(score_func=chi2, k=750)
kbest_chi.fit(X_train, y_train)

print("Feature selection", kbest_chi.get_support())
print("Feature scores", kbest_chi.scores_)
print("Selected features:", list(X.columns[kbest_chi.get_support()]))
print("Removed features:", list(X.columns[~kbest_chi.get_support()]))

Feature selection [False False False ... False  True  True]
Feature scores [ 18.61986511          nan   1.26100473 ...   0.22061648 160.24623579
 125.92347966]
Selected features: ['cv_name180', 'cv_name444', 'cv_name535', 'cv_name538', 'cv_name551', 'cv_name567', 'cv_name596', 'cv_name676', 'cv_name677', 'cv_name747', 'cv_name748', 'cv_name775', 'cv_name854', 'cv_name874', 'cv_name1017', 'cv_name1019', 'cv_name1131', 'cv_name1231', 'cv_name1288', 'cv_name1338', 'cv_name1339', 'cv_name1342', 'cv_name1362', 'cv_name1388', 'cv_name1400', 'cv_name1467', 'cv_name1480', 'cv_name1507', 'cv_name1567', 'cv_name1711', 'cv_name1714', 'cv_name1741', 'cv_name1917', 'cv_name1977', 'cv_name1999', 'cv_name2064', 'cv_name2095', 'cv_name2203', 'cv_name2212', 'cv_name2251', 'cv_name2348', 'cv_name2349', 'cv_name2352', 'cv_name2381', 'cv_name2514', 'cv_name2527', 'cv_name2531', 'cv_name2599', 'cv_name2617', 'cv_name2777', 'cv_name2899', 'cv_name3026', 'cv_name3030', 'cv_name3227', 'cv_name3578', 'cv_name3

In [114]:
# Transform (remove features not selected)
X_train_kbest_chi = kbest_chi.transform(X_train)
X_test_kbest_chi = kbest_chi.transform(X_test)

### Logistic regression

In [110]:
from sklearn.linear_model import LogisticRegression

Create logistic regression classfier

In [99]:
lrc_chi_clf = LogisticRegression(max_iter = 1000)

Test lrc on test,train. (0.2=test)

In [100]:
start = time.time()

lrc_chi_clf.fit(X_train_kbest_chi, y_train)

fin = time.time()

print(fin-start, 'seconds')

9.41276478767395 seconds


In [101]:
lrc_chi_clf.score(X_test_kbest_chi, y_test)

0.798125

### SVM

In [115]:
from sklearn.multiclass import OneVsRestClassifier
from sklearn.svm import SVC

Create logistic regression classfier

In [120]:
start = time.time()
svm_clf = SVC(kernel='rbf', random_state = 1)
svm_clf.fit(X_train_kbest_chi, y_train)
end = time.time()

Test lrc on test,train. (0.2=test)

In [121]:
end-start

1096.6597108840942

In [122]:
svm_clf.score(X_test_kbest_chi, y_test)

0.801125

### Selecting the best SVM

In [ ]:

# example of grid searching key hyperparametres for SVC
from sklearn.datasets import make_blobs
from sklearn.model_selection import RepeatedStratifiedKFold
from sklearn.model_selection import GridSearchCV
from sklearn.svm import SVC


# define model and parameters
model = SVC()
kernel = ['poly', 'rbf', 'sigmoid']
C = [50, 10, 1.0, 0.1, 0.01]
gamma = ['scale']
# define grid search
grid = dict(kernel=kernel,C=C,gamma=gamma)
cv = RepeatedStratifiedKFold(n_splits=10, n_repeats=3, random_state=1)
grid_search = GridSearchCV(estimator=model, param_grid=grid, n_jobs=-1, cv=cv, scoring='accuracy',error_score=0)
grid_result = grid_search.fit(X_train_kbest_chi, y_train)
# summarize results
print("Best: %f using %s" % (grid_result.best_score_, grid_result.best_params_))
means = grid_result.cv_results_['mean_test_score']
stds = grid_result.cv_results_['std_test_score']
params = grid_result.cv_results_['params']
for mean, stdev, param in zip(means, stds, params):
    print("%f (%f) with: %r" % (mean, stdev, param))

### Standardise data_test

In [102]:
# Core libraries
import pandas as pd

# Sklearn processing
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split

X_real_test_data = data_test_df

# Rescale the input features
scaler = MinMaxScaler(feature_range=(0,1))
X_real_test_data_ = scaler.fit_transform(X_real_test_data)
X_real_test_data = pd.DataFrame(X_real_test_data_, columns=X_real_test_data.columns)

In [104]:
data_test_chi = kbest_chi.transform(X_real_test_data)

In [ ]:
# X_test_kbest1000_reg

In [105]:
data_test_chi

array([[0.        , 0.        , 0.        , ..., 0.        , 0.11111111,
        0.37931034],
       [0.        , 0.        , 0.        , ..., 0.        , 0.03703704,
        0.03448276],
       [0.        , 0.        , 0.        , ..., 0.        , 0.09876543,
        0.31034483],
       ...,
       [0.        , 0.        , 0.        , ..., 0.        , 0.02469136,
        0.13793103],
       [0.        , 0.        , 0.        , ..., 0.        , 0.12345679,
        0.31034483],
       [0.        , 0.        , 0.        , ..., 0.        , 0.14814815,
        0.37931034]])

In [107]:
pred_chi_750 = lrc_chi_clf.predict(data_test_chi)

In [108]:
[i for i in pred_chi_750]

[2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 3.0,
 2.0,
 1.0,
 1.0,
 1.0,
 1.0,
 1.0,
 3.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 1.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 1.0,
 2.0,
 1.0,
 1.0,
 1.0,
 2.0,
 1.0,
 1.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 1.0,
 3.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 1.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 1.0

In [109]:
export_pred(pred_chi_750, "pred kbest 750 chi2")

id  duration_label
0         1             2.0
1         2             1.0
2         3             2.0
3         4             1.0
4         5             2.0
...     ...             ...
9995   9996             2.0
9996   9997             2.0
9997   9998             1.0
9998   9999             1.0
9999  10000             2.0

[10000 rows x 2 columns]

## Chi-sq k = 500

In [84]:
# Perform feature selection using a univariate statistical test
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2
kbest_chi = SelectKBest(score_func=chi2, k=500)
kbest_chi.fit(X_train, y_train)

print("Feature selection", kbest_chi.get_support())
print("Feature scores", kbest_chi.scores_)
print("Selected features:", list(X.columns[kbest_chi.get_support()]))
print("Removed features:", list(X.columns[~kbest_chi.get_support()]))

Feature selection [False False False ... False  True  True]
Feature scores [ 18.61986511          nan   1.26100473 ...   0.22061648 160.24623579
 125.92347966]
Selected features: ['cv_name180', 'cv_name444', 'cv_name535', 'cv_name567', 'cv_name596', 'cv_name676', 'cv_name677', 'cv_name747', 'cv_name854', 'cv_name874', 'cv_name1019', 'cv_name1288', 'cv_name1338', 'cv_name1339', 'cv_name1342', 'cv_name1388', 'cv_name1400', 'cv_name1467', 'cv_name1480', 'cv_name1507', 'cv_name1567', 'cv_name1711', 'cv_name1741', 'cv_name1977', 'cv_name2064', 'cv_name2095', 'cv_name2212', 'cv_name2251', 'cv_name2348', 'cv_name2349', 'cv_name2352', 'cv_name2381', 'cv_name2514', 'cv_name2527', 'cv_name2531', 'cv_name2599', 'cv_name2777', 'cv_name2899', 'cv_name3026', 'cv_name3227', 'cv_name3689', 'cv_name3816', 'cv_name3832', 'cv_name4164', 'cv_name4178', 'cv_name4632', 'cv_name4689', 'cv_name4929', 'cv_name5433', 'cv_name5522', 'cv_name5742', 'cv_name5756', 'cv_name6072', 'cv_name6115', 'cv_name6216', 'cv_n

In [85]:
# Transform (remove features not selected)
X_train_kbest_chi = kbest_chi.transform(X_train)
X_test_kbest_chi = kbest_chi.transform(X_test)

In [86]:
from sklearn.linear_model import LogisticRegression

Create logistic regression classfier

In [87]:
lrc_chi_clf = LogisticRegression(max_iter = 1000)

Test lrc on test,train. (0.2=test)

In [88]:
start = time.time()

lrc_chi_clf.fit(X_train_kbest_chi, y_train)

fin = time.time()

print(fin-start, 'seconds')

5.884264945983887 seconds


In [89]:
lrc_chi_clf.score(X_test_kbest_chi, y_test)

0.79575

## Chi-sq k = 10000

In [90]:
# Perform feature selection using a univariate statistical test
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import chi2
kbest_chi = SelectKBest(score_func=chi2, k=10000)
kbest_chi.fit(X_train, y_train)

print("Feature selection", kbest_chi.get_support())
print("Feature scores", kbest_chi.scores_)
print("Selected features:", list(X.columns[kbest_chi.get_support()]))
print("Removed features:", list(X.columns[~kbest_chi.get_support()]))

Feature selection [ True False False ... False  True  True]
Feature scores [ 18.61986511          nan   1.26100473 ...   0.22061648 160.24623579
 125.92347966]
Selected features: ['cv_name1', 'cv_name7', 'cv_name9', 'cv_name15', 'cv_name16', 'cv_name17', 'cv_name18', 'cv_name24', 'cv_name26', 'cv_name30', 'cv_name41', 'cv_name44', 'cv_name51', 'cv_name52', 'cv_name57', 'cv_name65', 'cv_name71', 'cv_name80', 'cv_name97', 'cv_name98', 'cv_name116', 'cv_name125', 'cv_name126', 'cv_name132', 'cv_name138', 'cv_name153', 'cv_name161', 'cv_name162', 'cv_name166', 'cv_name168', 'cv_name175', 'cv_name177', 'cv_name180', 'cv_name183', 'cv_name193', 'cv_name198', 'cv_name203', 'cv_name204', 'cv_name206', 'cv_name212', 'cv_name214', 'cv_name216', 'cv_name218', 'cv_name219', 'cv_name221', 'cv_name225', 'cv_name229', 'cv_name233', 'cv_name236', 'cv_name239', 'cv_name256', 'cv_name259', 'cv_name261', 'cv_name264', 'cv_name269', 'cv_name282', 'cv_name285', 'cv_name296', 'cv_name298', 'cv_name301', 'cv

In [91]:
# Transform (remove features not selected)
X_train_kbest_chi = kbest_chi.transform(X_train)
X_test_kbest_chi = kbest_chi.transform(X_test)

In [92]:
from sklearn.linear_model import LogisticRegression

Create logistic regression classfier

In [93]:
lrc_chi_clf = LogisticRegression(max_iter = 1000)

Test lrc on test,train. (0.2=test)

In [94]:
start = time.time()

lrc_chi_clf.fit(X_train_kbest_chi, y_train)

fin = time.time()

print(fin-start, 'seconds')

477.3719291687012 seconds


In [95]:
lrc_chi_clf.score(X_test_kbest_chi, y_test)

0.7895

### Select Kbest f_regression

In [36]:
# Split into train (2/3) and test (1/3) sets
# test_size = 0.33
# seed = 7
# X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=test_size, random_state=seed)
# print(X_train.shape)
# print(X_test.shape)

In [67]:
# Perform feature selection using a univariate statistical test
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif # use this for classification tasks
from sklearn.feature_selection import f_regression # use this for regression tasks

kbest1000_reg = SelectKBest(score_func=f_regression, k=1000)
kbest1000_reg.fit(X_train, y_train)

print("Feature selection", kbest1000_reg.get_support())
print("Feature scores", kbest1000_reg.scores_)
print("Selected features:", list(X.columns[kbest1000_reg.get_support()]))
# print("Removed features:", list(X.columns[~kbest1000_reg.get_support()]))

Feature selection [False False False ... False  True  True]
Feature scores [5.69213380e+00            nan 1.08931135e+00 ... 1.26859336e+01
 2.76548831e+03 2.55630071e+03]
Selected features: ['cv_name444', 'cv_name535', 'cv_name596', 'cv_name676', 'cv_name677', 'cv_name767', 'cv_name874', 'cv_name1019', 'cv_name1288', 'cv_name1342', 'cv_name1388', 'cv_name1479', 'cv_name1480', 'cv_name1507', 'cv_name1509', 'cv_name1567', 'cv_name1711', 'cv_name1741', 'cv_name1917', 'cv_name1977', 'cv_name1999', 'cv_name2203', 'cv_name2212', 'cv_name2251', 'cv_name2348', 'cv_name2349', 'cv_name2352', 'cv_name2381', 'cv_name2527', 'cv_name2531', 'cv_name2599', 'cv_name2899', 'cv_name3026', 'cv_name3164', 'cv_name3778', 'cv_name3797', 'cv_name3819', 'cv_name3832', 'cv_name4625', 'cv_name5492', 'cv_name5522', 'cv_name5529', 'cv_name5616', 'cv_name5742', 'cv_name5756', 'cv_name6072', 'cv_name6115', 'cv_name6213', 'cv_name6216', 'cv_name6329', 'cv_name6409', 'cv_name6432', 'cv_name7057', 'cv_name7140', 'cv_n

/Users/franklinaldo/opt/anaconda3/lib/python3.8/site-packages/sklearn/feature_selection/_univariate_selection.py:302: RuntimeWarning: invalid value encountered in true_divide
  corr /= X_norms
/Users/franklinaldo/opt/anaconda3/lib/python3.8/site-packages/scipy/stats/_distn_infrastructure.py:1932: RuntimeWarning: invalid value encountered in less_equal
  cond2 = cond0 & (x <= _a)


In [68]:
print("Selected features:", len(list(X.columns[kbest1000_reg.get_support()])))
print("Removed features:", len(list(X.columns[~kbest1000_reg.get_support()])))

Selected features: 1000
Removed features: 31067


In [69]:
# Transform (remove features not selected)
X_train_kbest1000_reg = kbest1000_reg.transform(X_train)
X_test_kbest1000_reg = kbest1000_reg.transform(X_test)

In [40]:
# print(X_train_kbest.shape)
# print(X_test_kbest.shape)

In [ ]:
# X_train

### Applying to logistic regression

In [71]:
from sklearn.linear_model import LogisticRegression

Create logistic regression classfier

In [72]:
lrc_kb1k_reg = LogisticRegression(max_iter = 1000)

Test lrc on test,train. (0.2=test)

In [73]:
start = time.time()

lrc_kb1k_reg.fit(X_train_kbest1000_reg, y_train)

fin = time.time()

print(fin-start, 'seconds')

47.93457889556885 seconds


In [74]:
lrc_kb1k_reg.score(X_test_kbest1000_reg, y_test)

0.800625

In [75]:
a = lrc_kb1k_reg.predict(X_test_kbest1000_reg)

In [76]:
X_test_kbest1000_reg

array([[0.        , 0.        , 0.        , ..., 0.60031235, 0.07407407,
        0.28205128],
       [0.        , 0.        , 0.        , ..., 0.5122728 , 0.04938272,
        0.02564103],
       [0.        , 0.        , 0.        , ..., 0.44638849, 0.11111111,
        0.15384615],
       ...,
       [0.        , 0.        , 0.        , ..., 0.57741534, 0.18518519,
        0.28205128],
       [0.        , 0.        , 0.        , ..., 0.45859107, 0.02469136,
        0.07692308],
       [0.        , 0.        , 0.        , ..., 0.50773485, 0.02469136,
        0.1025641 ]])

### Standardise data_test

In [77]:
# Core libraries
import pandas as pd

# Sklearn processing
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split

X = data_test_df

# Rescale the input features
scaler = MinMaxScaler(feature_range=(0,1))
X_ = scaler.fit_transform(X)
X = pd.DataFrame(X_, columns=X.columns)

In [45]:
X

In [79]:
data_test_kbest1000_reg = kbest1000_reg.transform(X)

In [43]:
# X_test_kbest1000_reg

In [81]:
data_test_kbest1000_reg

array([[0.        , 0.        , 0.        , ..., 0.46213788, 0.11111111,
        0.37931034],
       [0.        , 0.        , 0.        , ..., 0.54528404, 0.03703704,
        0.03448276],
       [0.        , 0.        , 0.        , ..., 0.65160752, 0.09876543,
        0.31034483],
       ...,
       [0.        , 0.        , 0.        , ..., 0.5837699 , 0.02469136,
        0.13793103],
       [0.        , 0.        , 0.        , ..., 0.51735375, 0.12345679,
        0.31034483],
       [0.        , 0.        , 0.        , ..., 0.51418664, 0.14814815,
        0.37931034]])

In [82]:
pred_kbest1k_reg = lrc_kb1k_reg.predict(data_test_kbest1000_reg)

In [83]:
[i for i in pred_kbest1k_reg]

[2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 3.0,
 2.0,
 1.0,
 1.0,
 1.0,
 1.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 1.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 1.0,
 3.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 1.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 1.0

In [84]:
export_pred(pred_kbest1k_reg, "pred kbest 1k reg")

id  duration_label
0         1             2.0
1         2             1.0
2         3             2.0
3         4             1.0
4         5             2.0
...     ...             ...
9995   9996             2.0
9996   9997             2.0
9997   9998             1.0
9998   9999             1.0
9999  10000             2.0

[10000 rows x 2 columns]

In [54]:

# del X_train_kbest1000_reg
# del X_test_kbest1000_reg 
# del lrc_kb1k_reg

# gc.collect()

## F-classifier 5000

In [55]:
# Perform feature selection using a univariate statistical test
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif # use this for classification tasks

kbest_clf = SelectKBest(score_func=f_classif, k=5000)
kbest_clf.fit(X_train, y_train)

print("Feature selection", kbest_clf.get_support())
print("Feature scores", kbest_clf.scores_)
print("Selected features:", list(X.columns[kbest_clf.get_support()]))
print("Removed features:", list(X.columns[~kbest_clf.get_support()]))

/Users/franklinaldo/opt/anaconda3/lib/python3.8/site-packages/sklearn/feature_selection/_univariate_selection.py:114: UserWarning: Features [    1    19    26 ... 31932 31962 31964] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx,
/Users/franklinaldo/opt/anaconda3/lib/python3.8/site-packages/sklearn/feature_selection/_univariate_selection.py:116: RuntimeWarning: invalid value encountered in true_divide
  f = msb / msw


Feature selection [ True False False ...  True  True  True]
Feature scores [9.31477083e+00            nan 6.30487805e-01 ... 7.07506007e+00
 1.89235783e+03 1.62967698e+03]
Selected features: ['cv_name1', 'cv_name7', 'cv_name15', 'cv_name16', 'cv_name18', 'cv_name24', 'cv_name26', 'cv_name51', 'cv_name52', 'cv_name65', 'cv_name71', 'cv_name97', 'cv_name125', 'cv_name153', 'cv_name175', 'cv_name180', 'cv_name183', 'cv_name193', 'cv_name206', 'cv_name219', 'cv_name233', 'cv_name259', 'cv_name261', 'cv_name285', 'cv_name296', 'cv_name304', 'cv_name317', 'cv_name318', 'cv_name333', 'cv_name351', 'cv_name353', 'cv_name354', 'cv_name370', 'cv_name386', 'cv_name424', 'cv_name432', 'cv_name444', 'cv_name459', 'cv_name487', 'cv_name510', 'cv_name516', 'cv_name528', 'cv_name535', 'cv_name538', 'cv_name540', 'cv_name546', 'cv_name551', 'cv_name562', 'cv_name564', 'cv_name567', 'cv_name579', 'cv_name582', 'cv_name585', 'cv_name586', 'cv_name596', 'cv_name597', 'cv_name602', 'cv_name636', 'cv_name64

In [56]:
# Transform (remove features not selected)
X_train_kbest_clf = kbest_clf.transform(X_train)
X_test_kbest_clf = kbest_clf.transform(X_test)

In [57]:
from sklearn.linear_model import LogisticRegression

Create logistic regression classfier

In [58]:
lrc_clf = LogisticRegression(max_iter = 1000)

Test lrc on test,train. (0.2=test)

In [59]:
start = time.time()

lrc_clf.fit(X_train_kbest_clf, y_train)

fin = time.time()

print(fin-start, 'seconds')

279.7264199256897 seconds


(8000, 5000)

In [62]:
lrc_clf.score(X_test_kbest_clf, y_test)

0.7975

### Standardise Test data

### Standardise data_test

In [45]:
# Core libraries
import pandas as pd

# Sklearn processing
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split

X_real_test_data = data_test_df

# Rescale the input features
scaler = MinMaxScaler(feature_range=(0,1))
X_real_test_data_ = scaler.fit_transform(X_real_test_data)
X_real_test_data = pd.DataFrame(X_real_test_data_, columns=X_real_test_data.columns)

In [45]:
X

In [47]:
data_test_kbest_clf = kbest_clf.transform(X_real_test_data)

In [43]:
# X_test_kbest1000_reg

In [48]:
data_test_kbest_clf

array([[0.        , 0.        , 0.        , ..., 0.43839986, 0.11111111,
        0.37931034],
       [0.        , 0.        , 0.        , ..., 0.38209555, 0.03703704,
        0.03448276],
       [0.        , 0.        , 0.        , ..., 0.56666764, 0.09876543,
        0.31034483],
       ...,
       [0.        , 0.        , 0.        , ..., 0.48035997, 0.02469136,
        0.13793103],
       [0.        , 0.        , 0.        , ..., 0.50492739, 0.12345679,
        0.31034483],
       [0.        , 0.        , 0.        , ..., 0.24966513, 0.14814815,
        0.37931034]])

In [50]:
pred_lrc_clf = lrc_clf.predict(data_test_kbest1000_classif)

In [51]:
[i for i in pred_lrc_clf]

[2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 3.0,
 2.0,
 1.0,
 1.0,
 1.0,
 1.0,
 1.0,
 1.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 1.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 1.0,
 1.0,
 3.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 1.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 1.0

In [52]:
export_pred(pred_lrc_clf, "pred kbest 5k clf")

id  duration_label
0         1             2.0
1         2             1.0
2         3             2.0
3         4             1.0
4         5             2.0
...     ...             ...
9995   9996             2.0
9996   9997             2.0
9997   9998             1.0
9998   9999             1.0
9999  10000             2.0

[10000 rows x 2 columns]

In [53]:

# del X_train_kbest1000_classif
# del X_test_kbest1000_classif 
# del lrc_kb1k_classif

# gc.collect()

In [38]:
# Perform feature selection using a univariate statistical test
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif # use this for classification tasks

kbest1000_classif = SelectKBest(score_func=f_classif, k=1000)
kbest1000_classif.fit(X_train, y_train)

print("Feature selection", kbest1000_classif.get_support())
print("Feature scores", kbest1000_classif.scores_)
print("Selected features:", list(X.columns[kbest1000_classif.get_support()]))
print("Removed features:", list(X.columns[~kbest1000_classif.get_support()]))

/Users/franklinaldo/opt/anaconda3/lib/python3.8/site-packages/sklearn/feature_selection/_univariate_selection.py:114: UserWarning: Features [    1    19    26 ... 31932 31962 31964] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx,
/Users/franklinaldo/opt/anaconda3/lib/python3.8/site-packages/sklearn/feature_selection/_univariate_selection.py:116: RuntimeWarning: invalid value encountered in true_divide
  f = msb / msw


Feature selection [False False False ... False  True  True]
Feature scores [9.31477083e+00            nan 6.30487805e-01 ... 7.07506007e+00
 1.89235783e+03 1.62967698e+03]
Selected features: ['cv_name444', 'cv_name596', 'cv_name676', 'cv_name677', 'cv_name747', 'cv_name775', 'cv_name874', 'cv_name1017', 'cv_name1019', 'cv_name1288', 'cv_name1338', 'cv_name1339', 'cv_name1342', 'cv_name1388', 'cv_name1480', 'cv_name1507', 'cv_name1567', 'cv_name1711', 'cv_name1741', 'cv_name1917', 'cv_name1977', 'cv_name1999', 'cv_name2095', 'cv_name2203', 'cv_name2212', 'cv_name2251', 'cv_name2348', 'cv_name2349', 'cv_name2352', 'cv_name2381', 'cv_name2514', 'cv_name2527', 'cv_name2531', 'cv_name2599', 'cv_name2777', 'cv_name2899', 'cv_name3026', 'cv_name3816', 'cv_name3832', 'cv_name4164', 'cv_name4178', 'cv_name4632', 'cv_name4689', 'cv_name4929', 'cv_name5433', 'cv_name5492', 'cv_name5522', 'cv_name5616', 'cv_name5742', 'cv_name5756', 'cv_name6072', 'cv_name6213', 'cv_name6216', 'cv_name6329', 'cv_n

In [39]:
# Perform feature selection using a univariate statistical test
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif # use this for classification tasks
from sklearn.feature_selection import f_regression # use this for regression tasks

kbest1000_classif = SelectKBest(score_func=f_classif, k=1000)
kbest1000_classif.fit(X_train, y_train)

print("Feature selection", kbest1000_classif.get_support())
print("Feature scores", kbest1000_classif.scores_)
print("Selected features:", list(X.columns[kbest1000_classif.get_support()]))
print("Removed features:", list(X.columns[~kbest1000_classif.get_support()]))

/Users/franklinaldo/opt/anaconda3/lib/python3.8/site-packages/sklearn/feature_selection/_univariate_selection.py:114: UserWarning: Features [    1    19    26 ... 31932 31962 31964] are constant.
  warnings.warn("Features %s are constant." % constant_features_idx,
/Users/franklinaldo/opt/anaconda3/lib/python3.8/site-packages/sklearn/feature_selection/_univariate_selection.py:116: RuntimeWarning: invalid value encountered in true_divide
  f = msb / msw


Feature selection [False False False ... False  True  True]
Feature scores [9.31477083e+00            nan 6.30487805e-01 ... 7.07506007e+00
 1.89235783e+03 1.62967698e+03]
Selected features: ['cv_name444', 'cv_name596', 'cv_name676', 'cv_name677', 'cv_name747', 'cv_name775', 'cv_name874', 'cv_name1017', 'cv_name1019', 'cv_name1288', 'cv_name1338', 'cv_name1339', 'cv_name1342', 'cv_name1388', 'cv_name1480', 'cv_name1507', 'cv_name1567', 'cv_name1711', 'cv_name1741', 'cv_name1917', 'cv_name1977', 'cv_name1999', 'cv_name2095', 'cv_name2203', 'cv_name2212', 'cv_name2251', 'cv_name2348', 'cv_name2349', 'cv_name2352', 'cv_name2381', 'cv_name2514', 'cv_name2527', 'cv_name2531', 'cv_name2599', 'cv_name2777', 'cv_name2899', 'cv_name3026', 'cv_name3816', 'cv_name3832', 'cv_name4164', 'cv_name4178', 'cv_name4632', 'cv_name4689', 'cv_name4929', 'cv_name5433', 'cv_name5492', 'cv_name5522', 'cv_name5616', 'cv_name5742', 'cv_name5756', 'cv_name6072', 'cv_name6213', 'cv_name6216', 'cv_name6329', 'cv_n

In [40]:
# Transform (remove features not selected)
X_train_kbest1000_classif = kbest1000_classif.transform(X_train)
X_test_kbest1000_classif = kbest1000_classif.transform(X_test)

In [41]:
from sklearn.linear_model import LogisticRegression

Create logistic regression classfier

In [42]:
lrc_kb1k_clf = LogisticRegression(max_iter = 1000)

Test lrc on test,train. (0.2=test)

In [43]:
start = time.time()

lrc_kb1k_clf.fit(X_train_kbest1000_classif, y_train)

fin = time.time()

print(fin-start, 'seconds')

57.86497616767883 seconds


In [44]:
lrc_kb1k_clf.score(X_test_kbest1000_classif, y_test)

0.8015

### Standardise Test data

### Standardise data_test

In [45]:
# Core libraries
import pandas as pd

# Sklearn processing
from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import train_test_split

X_real_test_data = data_test_df

# Rescale the input features
scaler = MinMaxScaler(feature_range=(0,1))
X_real_test_data_ = scaler.fit_transform(X_real_test_data)
X_real_test_data = pd.DataFrame(X_real_test_data_, columns=X_real_test_data.columns)

In [47]:
data_test_kbest1000_classif = kbest1000_classif.transform(X_real_test_data)

In [43]:
# X_test_kbest1000_reg

In [48]:
data_test_kbest1000_classif

array([[0.        , 0.        , 0.        , ..., 0.43839986, 0.11111111,
        0.37931034],
       [0.        , 0.        , 0.        , ..., 0.38209555, 0.03703704,
        0.03448276],
       [0.        , 0.        , 0.        , ..., 0.56666764, 0.09876543,
        0.31034483],
       ...,
       [0.        , 0.        , 0.        , ..., 0.48035997, 0.02469136,
        0.13793103],
       [0.        , 0.        , 0.        , ..., 0.50492739, 0.12345679,
        0.31034483],
       [0.        , 0.        , 0.        , ..., 0.24966513, 0.14814815,
        0.37931034]])

In [50]:
pred_kbest1k_classif = lrc_kb1k_clf.predict(data_test_kbest1000_classif)

In [51]:
[i for i in pred_kbest1k_classif]

[2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 3.0,
 2.0,
 1.0,
 1.0,
 1.0,
 1.0,
 1.0,
 1.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 1.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 1.0,
 1.0,
 1.0,
 3.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 1.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 1.0,
 1.0,
 2.0,
 2.0,
 2.0,
 2.0,
 1.0,
 2.0,
 2.0,
 2.0,
 1.0

In [52]:
export_pred(pred_kbest1k_classif, "pred kbest 1k classif")

id  duration_label
0         1             2.0
1         2             1.0
2         3             2.0
3         4             1.0
4         5             2.0
...     ...             ...
9995   9996             2.0
9996   9997             2.0
9997   9998             1.0
9998   9999             1.0
9999  10000             2.0

[10000 rows x 2 columns]

### kbest1500

In [39]:
# Perform feature selection using a univariate statistical test
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif # use this for classification tasks
from sklearn.feature_selection import f_regression # use this for regression tasks

kbest1500 = SelectKBest(score_func=f_regression, k=1500)
kbest1500.fit(X_train, y_train)

print("Feature selection", kbest1500.get_support())
print("Feature scores", kbest1500.scores_)
print("Selected features:", list(X.columns[kbest1500.get_support()]))
print("Removed features:", list(X.columns[~kbest1500.get_support()]))

Feature selection [False  True  True ... False  True  True]
Feature scores [3.73768470e-02 2.49638068e+01 2.04231999e+01 ...            nan
 2.26541372e+03 2.09864969e+03]
Selected features: ['d2v100_ingr2', 'd2v100_ingr3', 'd2v100_ingr4', 'd2v100_ingr6', 'd2v100_ingr8', 'd2v100_ingr12', 'd2v100_ingr13', 'd2v100_ingr14', 'd2v100_ingr21', 'd2v100_ingr22', 'd2v100_ingr25', 'd2v100_ingr27', 'd2v100_ingr29', 'd2v100_ingr32', 'd2v100_ingr35', 'd2v100_ingr36', 'd2v100_ingr39', 'd2v100_ingr42', 'd2v100_ingr47', 'd2v100_ingr53', 'd2v100_ingr57', 'd2v100_ingr60', 'd2v100_ingr62', 'd2v100_ingr66', 'd2v100_ingr70', 'd2v100_ingr72', 'd2v100_ingr73', 'd2v100_ingr74', 'd2v100_ingr75', 'd2v100_ingr77', 'd2v100_ingr78', 'd2v100_ingr81', 'd2v100_ingr85', 'd2v100_ingr88', 'd2v100_ingr91', 'd2v100_ingr92', 'd2v100_ingr93', 'd2v100_ingr94', 'd2v100_ingr95', 'd2v100_ingr97', 'd2v100_name1', 'd2v100_name2', 'd2v100_name3', 'd2v100_name5', 'd2v100_name6', 'd2v100_name7', 'd2v100_name8', 'd2v100_name9', 'd2v1

/Users/franklinaldo/opt/anaconda3/lib/python3.8/site-packages/sklearn/feature_selection/_univariate_selection.py:302: RuntimeWarning: invalid value encountered in true_divide
  corr /= X_norms
/Users/franklinaldo/opt/anaconda3/lib/python3.8/site-packages/scipy/stats/_distn_infrastructure.py:1932: RuntimeWarning: invalid value encountered in less_equal
  cond2 = cond0 & (x <= _a)


In [40]:
# Transform (remove features not selected)
X_train_kbest1500 = kbest1500.transform(X_train)
X_test_kbest1500 = kbest1500.transform(X_test)

### kbest 2000

In [19]:
# Perform feature selection using a univariate statistical test
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif # use this for classification tasks
from sklearn.feature_selection import f_regression # use this for regression tasks

kbest2000 = SelectKBest(score_func=f_regression, k=2000)
kbest2000.fit(X_train, y_train)

print("Feature selection", kbest2000.get_support())
print("Feature scores", kbest2000.scores_)
print("Selected features:", len(list(X.columns[kbest2000.get_support()])))
print("Removed features:", len(list(X.columns[~kbest2000.get_support()])))

/Users/franklinaldo/opt/anaconda3/lib/python3.8/site-packages/sklearn/feature_selection/_univariate_selection.py:302: RuntimeWarning: invalid value encountered in true_divide
  corr /= X_norms
/Users/franklinaldo/opt/anaconda3/lib/python3.8/site-packages/scipy/stats/_distn_infrastructure.py:1932: RuntimeWarning: invalid value encountered in less_equal
  cond2 = cond0 & (x <= _a)


Feature selection [False  True  True ... False  True  True]
Feature scores [3.73768470e-02 2.49638068e+01 2.04231999e+01 ...            nan
 2.26541372e+03 2.09864969e+03]
Selected features: ['d2v100_ingr2', 'd2v100_ingr3', 'd2v100_ingr4', 'd2v100_ingr6', 'd2v100_ingr7', 'd2v100_ingr8', 'd2v100_ingr12', 'd2v100_ingr13', 'd2v100_ingr14', 'd2v100_ingr21', 'd2v100_ingr22', 'd2v100_ingr23', 'd2v100_ingr25', 'd2v100_ingr27', 'd2v100_ingr29', 'd2v100_ingr32', 'd2v100_ingr35', 'd2v100_ingr36', 'd2v100_ingr39', 'd2v100_ingr42', 'd2v100_ingr43', 'd2v100_ingr44', 'd2v100_ingr46', 'd2v100_ingr47', 'd2v100_ingr48', 'd2v100_ingr53', 'd2v100_ingr57', 'd2v100_ingr60', 'd2v100_ingr62', 'd2v100_ingr66', 'd2v100_ingr70', 'd2v100_ingr71', 'd2v100_ingr72', 'd2v100_ingr73', 'd2v100_ingr74', 'd2v100_ingr75', 'd2v100_ingr76', 'd2v100_ingr77', 'd2v100_ingr78', 'd2v100_ingr81', 'd2v100_ingr85', 'd2v100_ingr88', 'd2v100_ingr91', 'd2v100_ingr92', 'd2v100_ingr93', 'd2v100_ingr94', 'd2v100_ingr95', 'd2v100_ingr97'

In [23]:
# Transform (remove features not selected)
X_train_kbest2000 = kbest2000.transform(X_train)
X_test_kbest2000 = kbest2000.transform(X_test)

## Select Kbest f_Classifier

# Create test and train set

In [24]:
X_train, X_test, Y_train, Y_test = train_test_split(data, duration_label, test_size=0.2)

Release memory

In [13]:
# import gc

In [10]:
# del countvec_name
# del countvec_steps
# del countvec_ingr
# del doc2vec_name
# del doc2vec_steps
# del doc2vec_ingr
# del data

# gc.collect()

80

# Logistic Regression

In [23]:
from sklearn.linear_model import LogisticRegression

Create logistic regression classfier

In [24]:
lrc = LogisticRegression(max_iter = 1000)

Test lrc on test,train. (0.2=test)

In [25]:
start = time.time()

lrc.fit(X_train_kbest1000, y_train)

fin = time.time()

print(fin-start, 'seconds')

53.3792188167572 seconds


In [26]:
lrc.score(X_test_kbest1000, y_test)

0.80075

### LRC kbest 1500

In [41]:
lrc1500 = LogisticRegression(max_iter = 1000)

In [45]:
start = time.time()

lrc1500.fit(X_train_kbest1500, y_train)

fin = time.time()

print(fin-start, 'seconds')

72.74154496192932 seconds


In [47]:
lrc1500.score(X_test_kbest1500, y_test)

0.7994696969696969

### LRC  kbest 2k

In [49]:
lrc2000 = LogisticRegression(max_iter = 1000)

In [50]:
start = time.time()

lrc2000.fit(X_train_kbest2000, y_train)

fin = time.time()

print(fin-start, 'seconds')

101.91791915893555 seconds


In [52]:
lrc2000.score(X_test_kbest2000, y_test)
# lrc2000.score(X_train_kbest2000, y_train)

0.7954545454545454